In [1]:
import numpy as np
import pandas as pd

jgbcm = pd.read_csv("https://www.mof.go.jp/jgbs/reference/interest_rate/jgbcm.csv", skiprows=1, encoding="shift-jis")
jgbcm_all = pd.read_csv("https://www.mof.go.jp/jgbs/reference/interest_rate/data/jgbcm_all.csv", skiprows=1, encoding="shift-jis")
interest_rate = pd.concat([jgbcm_all, jgbcm], axis=0).replace('-', np.nan)
shr = interest_rate["基準日"].str.extract("([SHR])(\d+).(\d+).(\d+)", expand=True)

# FIX: Use 'Int64' (nullable integer) to handle NaN values
shr[1] = shr[1].astype('Int64')

# The subsequent mask operations will now work with pd.NA values
shr[1] = shr[1].mask(shr[0]=="S", shr[1] + 25 + 1900)
shr[1] = shr[1].mask(shr[0]=="H", shr[1] - 12 + 2000)
shr[1] = shr[1].mask(shr[0]=="R", shr[1] + 18 + 2000)

# Convert back to string for date construction, then complete the process
shr[1] = shr[1].astype(str)
interest_rate["基準日"] = pd.to_datetime(shr[1] + "-" + shr[2] + "-" + shr[3])
interest_rate = interest_rate.set_index("基準日").stack().reset_index()
interest_rate.columns = ["基準日", "年限", "金利"]
interest_rate["年限"] = interest_rate["年限"].str.replace("年", "").astype(int)
interest_rate["金利"] = interest_rate["金利"].astype(float) / 100

interest_rate

<>:7: SyntaxWarning: invalid escape sequence '\d'
<>:7: SyntaxWarning: invalid escape sequence '\d'
/tmp/ipython-input-2007812472.py:7: SyntaxWarning: invalid escape sequence '\d'
  shr = interest_rate["基準日"].str.extract("([SHR])(\d+).(\d+).(\d+)", expand=True)


基準日  年限       金利
0      1974-09-24   1  0.10327
1      1974-09-24   2  0.09362
2      1974-09-24   3  0.08830
3      1974-09-24   4  0.08515
4      1974-09-24   5  0.08348
...           ...  ..      ...
160922 2025-12-09  15  0.02523
160923 2025-12-09  20  0.02917
160924 2025-12-09  25  0.03271
160925 2025-12-09  30  0.03334
160926 2025-12-09  40  0.03552

[160927 rows x 3 columns]

In [2]:
import plotly.express as px

fig = px.line(interest_rate,
              x="基準日",
              y="金利",
              color="年限"
)
fig.show()